In [1]:
import pandas as pd
import numpy as np
from math import radians, atan, tan, sin, acos, cos
from sklearn.cluster import DBSCAN
from sklearn import metrics
from sklearn.datasets.samples_generator import make_blobs
from sklearn.preprocessing import StandardScaler
from sklearn.cross_validation import train_test_split
import sklearn.cross_validation
from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = "all"

D:\Anaconda\lib\site-packages\sklearn\cross_validation.py:41: DeprecationWarning: This module was deprecated in version 0.18 in favor of the model_selection module into which all the refactored classes and functions are moved. Also note that the interface of the new CV iterators are different from that of this module. This module will be removed in 0.20.
  "This module will be removed in 0.20.", DeprecationWarning)


In [2]:
def getDistance(latA, lonA, latB, lonB):  
    ra = 6378140  # radius of equator: meter  
    rb = 6356755  # radius of polar: meter  
    flatten = (ra - rb) / ra  # Partial rate of the earth  
    # change angle to radians  
    radLatA = radians(latA)  
    radLonA = radians(lonA)  
    radLatB = radians(latB)  
    radLonB = radians(lonB)  
  
    try: 
        pA = atan(rb / ra * tan(radLatA))  
        pB = atan(rb / ra * tan(radLatB))  
        x = acos(sin(pA) * sin(pB) + cos(pA) * cos(pB) * cos(radLonA - radLonB))  
        c1 = (sin(x) - x) * (sin(pA) + sin(pB))**2 / cos(x / 2)**2  
        c2 = (sin(x) + x) * (sin(pA) - sin(pB))**2 / sin(x / 2)**2  
        dr = flatten / 8 * (c1 - c2)  
        distance = ra * (x + dr)  
        return distance  # meter   
    except:
        return 0.0000001
    
def score(latA, lonA, latB, lonB): #计算分数
    res = 0
    for i in range(len(latA)):
        d = getDistance(latA[i], lonA[i], latB[i], lonB[i])
        res += 1. / (1. + np.exp(-(d-1000)/250.))
    return res / len(latA)

In [3]:
good_train = pd.read_csv('D:/bmsz/good_train.csv', low_memory=False)
good_test = pd.read_csv('D:/bmsz/good_test.csv', low_memory=False)
train = pd.read_csv('D:/bmsz/train_new.csv', low_memory=False)
test = pd.read_csv('D:/bmsz/test_new.csv', low_memory=False)

In [4]:
(good_test['start_block'] == -1).sum()
(good_test['out_id'].isin(good_train['out_id'])).sum()

11519

58097

In [5]:
'''
def get_max_dis(df):
    res = 0
    for i in range(len(df)):
        res = max(res, getDistance(df.iloc[i]['start_lat'], df.iloc[i]['start_lon'],df.iloc[i]['end_lat'],df.iloc[i]['end_lon']))
    return res
train.groupby('out_id').apply(lambda x: get_max_dis(x))
'''

"\ndef get_max_dis(df):\n    res = 0\n    for i in range(len(df)):\n        res = max(res, getDistance(df.iloc[i]['start_lat'], df.iloc[i]['start_lon'],df.iloc[i]['end_lat'],df.iloc[i]['end_lon']))\n    return res\ntrain.groupby('out_id').apply(lambda x: get_max_dis(x))\n"

In [7]:
good_train.groupby('out_id').apply(lambda x: len(x)).reset_index().describe()
train.groupby('out_id').apply(lambda x: len(x)).reset_index().describe()

0
count  5817.000000
mean    177.707065
std      98.088275
min       2.000000
25%     101.000000
50%     156.000000
75%     240.000000
max     510.000000

0
count  5817.000000
mean    257.145264
std     101.075236
min      87.000000
25%     175.000000
50%     238.000000
75%     328.000000
max     582.000000

#### 加入时间特征

In [6]:
def add_time_feature(df):
    #2018/01/01-2018/10/31的节日与特殊工作日
    special_holiday = ['2018-01-01'] + ['2018-02-%d' % d for d in range(15, 22)] + \
                      ['2018-04-%2d' % d for d in range(5, 8)] + \
                      ['2018-04-%d' % d for d in range(29, 31)] + ['2018-05-01'] +\
                      ['2018-06-%d' % d for d in range(16, 19)] + \
                      ['2018-09-%d' % d for d in range(22, 25)] + \
                      ['2018-10-%2d' % d for d in range(1, 8)]
    special_workday = ['2018-02-%d' % d for d in [11, 24]] + \
                      ['2018-04-08'] + ['2018-04-28'] + \
                      ['2018-09-%d' % d for d in range(29, 31)]
    date = 'start_time'
    tmp_col = df[date].map(pd.Timestamp)
    df['hour'] = tmp_col.map(lambda t: t.hour)
    df['half'] = tmp_col.map(lambda t: t.minute // 30)
    df['day'] = tmp_col.map(lambda t: t.dayofweek)
    tmp_date_col = df[date].map(lambda t: t[:10])
    df['is_special_holiday'] = tmp_date_col.isin(special_holiday).astype(int)
    df['normal_weekend'] = (df['day'] >= 5 & ~df['is_special_holiday']).astype(int)
add_time_feature(train)
add_time_feature(test)

In [7]:
train = train.drop(['r_key', 'start_time', 'end_time'], axis=1)
test_r_key = test['r_key']
test = test.drop(['r_key', 'start_time'], axis=1)

In [8]:
train.head()

out_id  start_lat   start_lon    end_lat     end_lon  hour  half  \
0  2016061820000b  33.783415  111.603660  33.779811  111.605885    10     0   
1  2016061820000b  34.810763  115.549264  34.814875  115.549374    17     1   
2  2016061820000b  34.640284  115.539024  34.813136  115.559243    14     1   
3  2016061820000b  34.818280  115.542039  34.813141  115.559217    17     0   
4  2016061820000b  34.813278  115.559260  34.786126  115.874361    18     0   

   day  is_special_holiday  normal_weekend  
0    5                   0               1  
1    0                   0               0  
2    1                   0               0  
3    1                   0               0  
4    1                   0               0

In [12]:
car_data_dict = {}
count = 0
for car_id, data in train.groupby('out_id'):
    car_data_dict[car_id] = [data.drop('out_id', axis=1), []] #第二个用于存放其他所需的内容，如学习器等
    count += 1
    if count % 100 == 0:  print(count)

100
200
300
400
500
600
700
800
900
1000
1100
1200
1300
1400
1500
1600
1700
1800
1900
2000
2100
2200
2300
2400
2500
2600
2700
2800
2900
3000
3100
3200
3300
3400
3500
3600
3700
3800
3900
4000
4100
4200
4300
4400
4500
4600
4700
4800
4900
5000
5100
5200
5300
5400
5500
5600
5700
5800


In [13]:
interval = 0.005

def get_i_label(row, lat_ran):
    i = 0
    while lat_ran[i+1] < row: i += 1
    return i

def get_j_label(row, lon_ran):
    j = 0
    while lon_ran[j+1] < row: j += 1
    return j

def process_one_car(car_id):
    df = car_data_dict[car_id][0]
    max_lat = max(df['start_lat'].max(), df['end_lat'].max())
    min_lat = min(df['start_lat'].min(), df['end_lat'].min())
    max_lon = max(df['start_lon'].max(), df['end_lon'].max())
    min_lon = min(df['start_lon'].min(), df['end_lon'].min())
    interval = 0.005
    while 1:
        lat_ran = np.arange(min_lat, max_lat + interval, interval)
        lon_ran = np.arange(min_lon, max_lon + interval, interval)
        tmp = df['end_lat'].apply(lambda r: get_i_label(r, lat_ran)) +  \
            df['end_lat'].apply(lambda r: get_j_label(r, lon_ran)) * len(lat_ran)
        if len(tmp.value_counts()) < 10: break
        interval += 0.005
    df['block'] = tmp
    end_lat_mean = df.groupby('block')['end_lat'].mean()
    end_lon_mean = df.groupby('block')['end_lon'].mean()
    car_data_dict[car_id][1].append(tmp)
    car_data_dict[car_id][1].append(df[['end_lat', 'end_lon']])
    car_data_dict[car_id][1].append([end_lat_mean, end_lon_mean])
    df = df.drop(['end_lat', 'end_lon', 'block'], axis=1)
    car_data_dict[car_id][0] = df

In [14]:
count = 0
for car_id, data in train.groupby('out_id'):
    process_one_car(car_id)
    count += 1
    if count % 100 == 0:  print(count)

100
200
300
400
500
600
700
800
900
1000
1100
1200
1300
1400
1500
1600
1700
1800
1900
2000
2100
2200
2300
2400
2500
2600
2700
2800
2900
3000
3100
3200
3300
3400
3500
3600
3700
3800
3900
4000
4100
4200
4300
4400
4500
4600
4700
4800
4900
5000
5100
5200
5300
5400
5500
5600
5700
5800


#### 验证集

In [104]:
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import RandomForestClassifier, AdaBoostClassifier, GradientBoostingClassifier
from sklearn.naive_bayes import MultinomialNB
import copy
clfs = [DecisionTreeClassifier(), RandomForestClassifier(), MultinomialNB(), AdaBoostClassifier(), GradientBoostingClassifier()]

def calc_score(y_pre, y_vali_lat_lon, lat_lon_mean):
    end_lat_mean, end_lon_mean = lat_lon_mean[0], lat_lon_mean[1]
    pre_lat, pre_lon = np.zeros(len(y_pre)),np.zeros(len(y_pre))
    for i in range(len(y_pre)):
        pre_lat[i] = end_lat_mean[y_pre[i]]
        pre_lon[i] = end_lon_mean[y_pre[i]]
    vali_lat = y_vali_lat_lon[:,0]
    vali_lon = y_vali_lat_lon[:,1]
    return score(pre_lat, pre_lon, vali_lat, vali_lon)
    
score_all = [[0,0] for i in range(5)]
def train_one_car(car_id):
    data, label = car_data_dict[car_id][0], car_data_dict[car_id][1][0]
    x_train, x_vali, y_train, y_vali = train_test_split(data, label, test_size=0.1, random_state=1)
    clfs_ = []
    for i,clf in enumerate(clfs):
        if len(np.unique(y_train.values)) == 1:
            y_pre = [y_train.values[0] for _ in range(len(y_vali))]
            clfs_.append(y_train.values[0])
        else:
            clf = copy.deepcopy(clf)
            clf.fit(x_train, y_train)
            y_pre = clf.predict(x_vali)
            clfs_.append(clf)
        print(i, 'Accuracy is: ', (y_pre == y_vali).sum() / len(y_vali))
        print(y_pre)
        print(y_vali)
        start_index = car_data_dict[car_id][1][1].index[0]
        temp_score = calc_score(y_pre, car_data_dict[car_id][1][1].values[y_vali.index - start_index], car_data_dict[car_id][1][2])
        print('Score is: ', temp_score)
        car_data_dict[car_id][1].append(clfs_)
        score_all[i][0] += temp_score * len(y_pre)
        score_all[i][1] += len(y_pre)

In [105]:
count = 0
for car_id, data in train.groupby('out_id'):
    train_one_car(car_id)
    count += 1
    if count % 100 == 0:  print(count)

0 Accuracy is:  0.769230769231
Score is:  0.244604776899
1 Accuracy is:  0.769230769231
Score is:  0.244604776899
2 Accuracy is:  0.615384615385
Score is:  0.395683821519
3 Accuracy is:  0.769230769231
Score is:  0.244604776899
4 Accuracy is:  0.846153846154
Score is:  0.169065254589
0 Accuracy is:  1.0
Score is:  0.0179897778428
1 Accuracy is:  0.96875
Score is:  0.0486777087813
2 Accuracy is:  0.78125
Score is:  0.232804874662
3 Accuracy is:  1.0
Score is:  0.0179897778428
4 Accuracy is:  1.0
Score is:  0.0179897778428
0 Accuracy is:  1.0
Score is:  0.0179862099692
1 Accuracy is:  1.0
Score is:  0.0179862099692
2 Accuracy is:  0.8
Score is:  0.214388967975
3 Accuracy is:  1.0
Score is:  0.0179862099692
4 Accuracy is:  1.0
Score is:  0.0179862099692
0 Accuracy is:  0.944444444444
Score is:  0.0725425316375
1 Accuracy is:  0.944444444444
Score is:  0.0725425316375
2 Accuracy is:  0.611111111111
Score is:  0.399880461648
3 Accuracy is:  0.944444444444
Score is:  0.0725425316375
4 Accura

4 Accuracy is:  1.0
Score is:  0.0179906283886
0 Accuracy is:  1.0
Score is:  0.0179862099692
1 Accuracy is:  1.0
Score is:  0.0179862099692
2 Accuracy is:  1.0
Score is:  0.0179862099692
3 Accuracy is:  1.0
Score is:  0.0179862099692
4 Accuracy is:  1.0
Score is:  0.0179862099692
0 Accuracy is:  1.0
Score is:  0.0179862099692
1 Accuracy is:  1.0
Score is:  0.0179862099692
2 Accuracy is:  1.0
Score is:  0.0179862099692
3 Accuracy is:  1.0
Score is:  0.0179862099692
4 Accuracy is:  1.0
Score is:  0.0179862099692
0 Accuracy is:  1.0
Score is:  0.0179862099692
1 Accuracy is:  1.0
Score is:  0.0179862099692
2 Accuracy is:  0.967741935484
Score is:  0.0496640741637
3 Accuracy is:  1.0
Score is:  0.0179862099692
4 Accuracy is:  1.0
Score is:  0.0179862099692
0 Accuracy is:  0.962962962963
Score is:  0.0543573398221
1 Accuracy is:  0.962962962963
Score is:  0.0543573398221
2 Accuracy is:  0.888888888889
Score is:  0.127098853306
3 Accuracy is:  0.962962962963
Score is:  0.0543573398221
4 Accu

3 Accuracy is:  0.869565217391
Score is:  0.146074965191
4 Accuracy is:  0.95652173913
Score is:  0.0606824617096
0 Accuracy is:  0.9375
Score is:  0.0793620718461
1 Accuracy is:  0.9375
Score is:  0.0793620718461
2 Accuracy is:  0.875
Score is:  0.140737933723
3 Accuracy is:  0.9375
Score is:  0.0793620718461
4 Accuracy is:  0.9375
Score is:  0.0793620718461
0 Accuracy is:  0.923076923077
Score is:  0.0935257322792
1 Accuracy is:  0.923076923077
Score is:  0.0935257322792
2 Accuracy is:  0.923076923077
Score is:  0.0935257322792
3 Accuracy is:  0.923076923077
Score is:  0.0935257322792
4 Accuracy is:  0.923076923077
Score is:  0.0935257322792
0 Accuracy is:  1.0
Score is:  0.0179862099692
1 Accuracy is:  1.0
Score is:  0.0179862099692
2 Accuracy is:  1.0
Score is:  0.0179862099692
3 Accuracy is:  1.0
Score is:  0.0179862099692
4 Accuracy is:  1.0
Score is:  0.0179862099692
0 Accuracy is:  0.916666666667
Score is:  0.0998206924717
1 Accuracy is:  0.916666666667
Score is:  0.09982069247

4 Accuracy is:  1.0
Score is:  0.0179943989609
0 Accuracy is:  0.857142857143
Score is:  0.1582786914
1 Accuracy is:  0.857142857143
Score is:  0.1582786914
2 Accuracy is:  0.714285714286
Score is:  0.29856637569
3 Accuracy is:  0.857142857143
Score is:  0.1582786914
4 Accuracy is:  0.857142857143
Score is:  0.1582786914
0 Accuracy is:  0.954545454545
Score is:  0.0626232004251
1 Accuracy is:  0.977272727273
Score is:  0.0403047051971
2 Accuracy is:  0.954545454545
Score is:  0.0626232004251
3 Accuracy is:  0.977272727273
Score is:  0.0403047051971
4 Accuracy is:  0.954545454545
Score is:  0.0626232004251
0 Accuracy is:  1.0
Score is:  0.0179862099692
1 Accuracy is:  1.0
Score is:  0.0179862099692
2 Accuracy is:  0.947368421053
Score is:  0.0696711462866
3 Accuracy is:  1.0
Score is:  0.0179862099692
4 Accuracy is:  1.0
Score is:  0.0179862099692
100
0 Accuracy is:  1.0
Score is:  0.0179862099692
1 Accuracy is:  1.0
Score is:  0.0179862099692
2 Accuracy is:  1.0
Score is:  0.0179862099

4 Accuracy is:  0.974358974359
Score is:  0.0431660507392
0 Accuracy is:  1.0
Score is:  0.0179927444532
1 Accuracy is:  1.0
Score is:  0.0179927444532
2 Accuracy is:  0.972972972973
Score is:  0.0445336576973
3 Accuracy is:  1.0
Score is:  0.0179927444532
4 Accuracy is:  1.0
Score is:  0.0179927444532
0 Accuracy is:  1.0
Score is:  0.0179862099692
1 Accuracy is:  1.0
Score is:  0.0179862099692
2 Accuracy is:  0.666666666667
Score is:  0.345324139979
3 Accuracy is:  0.777777777778
Score is:  0.236211496643
4 Accuracy is:  0.962962962963
Score is:  0.0543570910814
0 Accuracy is:  1.0
Score is:  0.0179903141898
1 Accuracy is:  0.972222222222
Score is:  0.045268475024
2 Accuracy is:  0.861111111111
Score is:  0.154380558694
3 Accuracy is:  0.972222222222
Score is:  0.045268475024
4 Accuracy is:  1.0
Score is:  0.0179903141898
0 Accuracy is:  1.0
Score is:  0.0179862099692
1 Accuracy is:  1.0
Score is:  0.0179862099692
2 Accuracy is:  0.972222222222
Score is:  0.0452643708033
3 Accuracy is

...

3 Accuracy is:  0.88
Score is:  0.135827864773
4 Accuracy is:  0.92
Score is:  0.0965473131716
0 Accuracy is:  0.95652173913
Score is:  0.0606824617096
1 Accuracy is:  0.95652173913
Score is:  0.0606824617096
2 Accuracy is:  0.913043478261
Score is:  0.10337871345
3 Accuracy is:  0.95652173913
Score is:  0.0606824617096
4 Accuracy is:  0.95652173913
Score is:  0.0606824617096
0 Accuracy is:  0.975609756098
Score is:  0.0419377658236
1 Accuracy is:  0.975609756098
Score is:  0.0419377658236
2 Accuracy is:  0.975609756098
Score is:  0.0419377658236
3 Accuracy is:  0.975609756098
Score is:  0.0419377658236
4 Accuracy is:  0.975609756098
Score is:  0.0419377658236
0 Accuracy is:  0.962962962963
Score is:  0.0543570910814
1 Accuracy is:  0.925925925926
Score is:  0.0907279721937
2 Accuracy is:  0.740740740741
Score is:  0.272582377755
3 Accuracy is:  0.925925925926
Score is:  0.0907279721937
4 Accuracy is:  1.0
Score is:  0.0179862099692
0 Accuracy is:  1.0
Score is:  0.0179862099692
1 Accu

4 Accuracy is:  1.0
Score is:  0.0179862099692
0 Accuracy is:  0.933333333333
Score is:  0.0834542437044
1 Accuracy is:  0.866666666667
Score is:  0.148921381973
2 Accuracy is:  0.733333333333
Score is:  0.279856553977
3 Accuracy is:  0.933333333333
Score is:  0.0834542437044
4 Accuracy is:  0.933333333333
Score is:  0.0834542437044
0 Accuracy is:  1.0
Score is:  0.017987125787
1 Accuracy is:  0.954545454545
Score is:  0.0626241162429
2 Accuracy is:  0.863636363636
Score is:  0.151897181337
3 Accuracy is:  0.863636363636
Score is:  0.151897181337
4 Accuracy is:  1.0
Score is:  0.017987125787
0 Accuracy is:  1.0
Score is:  0.0179862099692
1 Accuracy is:  1.0
Score is:  0.0179862099692
2 Accuracy is:  0.761904761905
Score is:  0.251799017119
3 Accuracy is:  1.0
Score is:  0.0179862099692
4 Accuracy is:  1.0
Score is:  0.0179862099692
0 Accuracy is:  1.0
Score is:  0.0179862099692
1 Accuracy is:  1.0
Score is:  0.0179862099692
2 Accuracy is:  0.952380952381
Score is:  0.0647487713992
3 Ac

3 Accuracy is:  0.740740740741
Score is:  0.272582377755
4 Accuracy is:  0.925925925926
Score is:  0.0907279721937
0 Accuracy is:  1.0
Score is:  0.0179862099692
1 Accuracy is:  1.0
Score is:  0.0179862099692
2 Accuracy is:  1.0
Score is:  0.0179862099692
3 Accuracy is:  1.0
Score is:  0.0179862099692
4 Accuracy is:  1.0
Score is:  0.0179862099692
0 Accuracy is:  1.0
Score is:  0.0179862099692
1 Accuracy is:  1.0
Score is:  0.0179862099692
2 Accuracy is:  1.0
Score is:  0.0179862099692
3 Accuracy is:  1.0
Score is:  0.0179862099692
4 Accuracy is:  1.0
Score is:  0.0179862099692
0 Accuracy is:  1.0
Score is:  0.0179862099692
1 Accuracy is:  0.944444444444
Score is:  0.0725425316375
2 Accuracy is:  0.944444444444
Score is:  0.0725425316375
3 Accuracy is:  1.0
Score is:  0.0179862099692
4 Accuracy is:  1.0
Score is:  0.0179862099692
0 Accuracy is:  0.979166666667
Score is:  0.0384448305948
1 Accuracy is:  0.979166666667
Score is:  0.0384448305948
2 Accuracy is:  0.875
Score is:  0.1407379

4 Accuracy is:  1.0
Score is:  0.0179915364499
0 Accuracy is:  1.0
Score is:  0.0179862099692
1 Accuracy is:  1.0
Score is:  0.0179862099692
2 Accuracy is:  1.0
Score is:  0.0179862099692
3 Accuracy is:  1.0
Score is:  0.0179862099692
4 Accuracy is:  1.0
Score is:  0.0179862099692
0 Accuracy is:  1.0
Score is:  0.0179862099692
1 Accuracy is:  1.0
Score is:  0.0179862099692
2 Accuracy is:  1.0
Score is:  0.0179862099692
3 Accuracy is:  1.0
Score is:  0.0179862099692
4 Accuracy is:  1.0
Score is:  0.0179862099692
0 Accuracy is:  0.909090909091
Score is:  0.107260190881
1 Accuracy is:  0.909090909091
Score is:  0.107260190881
2 Accuracy is:  0.909090909091
Score is:  0.107260190881
3 Accuracy is:  0.909090909091
Score is:  0.107260190881
4 Accuracy is:  0.909090909091
Score is:  0.107260190881
0 Accuracy is:  1.0
Score is:  0.0179862099692
1 Accuracy is:  1.0
Score is:  0.0179862099692
2 Accuracy is:  0.5
Score is:  0.508993104985
3 Accuracy is:  0.95
Score is:  0.0670868994707
4 Accuracy

4 Accuracy is:  0.954545454545
Score is:  0.0626232004251


In [106]:
for i, scores_with_len in enumerate(score_all):
    print(i, "score = ", score_with_len[0] / scores_with_len[1])

NameError: name 'score_with_len' is not defined

#### 训练全部数据

In [15]:
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import RandomForestClassifier, AdaBoostClassifier, GradientBoostingClassifier
from sklearn.naive_bayes import MultinomialNB
from xgboost import XGBClassifier
import copy
clfs = [DecisionTreeClassifier(), RandomForestClassifier(), MultinomialNB(), 
        AdaBoostClassifier(), GradientBoostingClassifier(), XGBClassifier()]
    
def train_one_car(car_id):
    x_train, y_train = car_data_dict[car_id][0], car_data_dict[car_id][1][0]
    clfs_ = []
    for i,clf in enumerate(clfs):
        if len(np.unique(y_train.values)) == 1:
            clfs_.append(y_train.values[0])
        else:
            clf = copy.deepcopy(clf)
            clf.fit(x_train, y_train)
            clfs_.append(clf)
        car_data_dict[car_id][1].append(clfs_)

In [16]:
count = 0
for car_id, data in train.groupby('out_id'):
    train_one_car(car_id)
    count += 1
    if count % 100 == 0:  print(count)

100
200
300
400
500
600
700
800
900
1000
1100
1200
1300
1400
1500
1600
1700
1800
1900
2000
2100
2200
2300
2400
2500
2600
2700
2800
2900
3000
3100
3200
3300
3400
3500
3600
3700
3800
3900
4000
4100
4200
4300
4400
4500
4600
4700
4800
4900
5000
5100
5200
5300
5400
5500
5600
5700
5800


#### 预测

In [17]:
def predict_one_test(to_predict, clf_num=1):
    car_id = to_predict['out_id'].iloc[0]
    print(car_id)
    to_predict = to_predict.drop('out_id', axis=1)
    if type(car_data_dict[car_id][1][3][clf_num]) == np.int64:
        y_pre = car_data_dict[car_id][1][3][clf_num]
    else:
        y_pre = car_data_dict[car_id][1][3][clf_num].predict(to_predict)[0] #block值
    print(np.array([car_data_dict[car_id][1][2][0][y_pre], car_data_dict[car_id][1][2][1][y_pre]]))
    return np.array([car_data_dict[car_id][1][2][0][y_pre], car_data_dict[car_id][1][2][1][y_pre]]) #转换成经纬度

In [18]:
def predict_all(test, clf_num=0):
    y_pre = np.zeros((len(test),2))
    for i in range(len(test)):
        y_pre[i] = predict_one_test(test.iloc[i:i+1], clf_num)
    return y_pre

In [ ]:
y_pre = predict_all(test,5)
sub = pd.DataFrame({'r_key': test_r_key, 'end_lat': y_pre[:,0], 'end_lon': y_pre[:,1]})
sub = sub[['r_key', 'end_lat', 'end_lon']]
sub.to_csv(r'D:\bmsz\sub.csv', index=None)

358962079107966
[  43.9498076   125.31301469]
358962079111695
[  43.8832871   125.27863426]
358962079120563
[  43.80112358  125.28611014]
4A23256745CBA3B0
[  32.58071433  115.11094367]
851181601098201
[  22.68338343  113.30911514]
861021508005421
[  37.69815531  106.51367727]
861021509004701
[  30.74443543  121.31369732]
861021509017441
[  36.0243168   106.27474964]
861021510007852
[ 44.3094008   86.05979877]
861021510025842
[  38.49706697  115.58739028]
861021510042922
[  29.36051599  113.17888361]
861081604013621
[  37.5125129   117.73074864]
861081605012111
[  33.2240194   107.52854518]
861181511039231
[  31.75396703  116.50341065]
861181511041831
[  31.29264977  121.32394932]
861181511047051
[  24.99007248  102.72461531]
861181511148251
[  25.50650295  103.81367933]
861181511171241
[  28.16233177  112.99869768]
861181511171991
[  30.51023093  111.40300517]
861181511175991
[  40.20848937  117.95239736]
861181511195261
[  22.62312245  114.01981612]
861181511300201
[  26.26295037  116

[  34.78812328  113.63585041]
861691610019041
[  34.36278046  107.19454641]
861691610019161
[  27.26147792  111.74193232]
861691610019581
[  36.78905017  119.48286549]
861691610021271
[  38.91866739  121.60543969]
861691610021411
[  37.4460657   117.95768333]
861691610021611
[  34.10828397  108.31839128]
861691610021851
[  22.54865244  114.07921598]
861691610022261
[  22.91940858  113.98040674]
861691610024721
[  31.40569911  121.42956494]
861691610024791
[  34.2285001   108.94688419]
861691610024801
[  31.0418128   107.51725373]
861691610024851
[  25.05282525  102.82724184]
861691610026241
[  31.62281747  120.82451037]
861691610026981
[  30.63910907  114.10538024]
861691610027061
[  24.34517291  102.54654673]
861691610027121
[  31.64731777  120.80758752]
861691610027151
[  36.07560752  106.22664098]
861691610027181
[  39.18234584  117.09650069]
861691610027791
[  35.58231406  110.75657645]
861691610030011
[  31.45262667  104.74295433]
861691610030881
[ 37.20113096  79.80599651]
861691

[ 43.92764525  87.60056443]
861691611088981
[  31.35740188  107.79050096]
861691611089661
[  34.94718088  109.60620903]
861691611090111
[  26.57411177  101.70273366]
861691611090261
[  31.0853898   107.87166969]
861691611091991
[ 36.93119199  98.47493039]
861691611200081
[  23.14401915  113.09868295]
861691611200151
[  22.64519825  114.18046755]
861691611200251
[  28.56592505  121.38545817]
861691611200271
[  31.12158646  121.39424863]
861691611200291
[  25.69557027  114.33475835]
861691611200331
[  30.57652204  114.3686151 ]
861691611200351
[  30.73397421  111.30646247]
861691611200511
[  39.87668734  116.38464668]
861691611200531
[  32.02382716  120.85676067]
861691611200601
[  27.25669904  111.57062751]
861691611200741
[  31.20507278  121.40601195]
861691611201361
[  29.98887873  120.60486471]
861691611201851
[  28.19117379  120.7567377 ]
861691611201861
[  39.61582942  118.11384692]
861691611202041
[  28.65426368  121.29097886]
861691611202351
[  26.8841886  112.5780722]
8616916112

861691707003971
[  30.28980823  108.91966233]
861691707005051
[  36.64418073  101.74512247]
861691707005661
[  31.54023535  120.33429818]
861691707006831
[  40.81617433  111.75070139]
861691707007581
[  29.02163019  119.17460764]
861691707008281
[  28.18266057  104.46932845]
861691707009831
[  34.72303225  112.68135118]
861691707009981
[  29.04210956  111.56579681]
861691709013941
[  36.54251579  101.69393981]
861691709024881
[  30.23109636  120.1507773 ]
861691709025371
[  39.90381601  119.51393965]
861691709025941
[  37.68004774  115.86418678]
861691709026051
[  23.11596933  113.39579123]
861691709026141
[  38.69009374  116.09913443]
861691709026411
[  30.61003181  114.37238128]
861691709026701
[  31.25646647  121.43297843]
861691709028201
[  23.10410743  113.45803791]
861691709028711
[  29.65702469  106.57455415]
861691709028761
[  29.27182406  106.20748818]
861691709028771
[  27.74262309  120.61066535]
861691709028891
[  31.02567637  120.57311048]
861691709029231
[  36.68093923  11

[  21.96557691  110.92555368]
861821706038151
[ 43.94391432  81.42403835]
861821706039191
[ 39.4375563   76.01656367]
861821706041271
[  36.56780489  101.86432263]
861821706041411
[  26.89594245  109.76269843]
861821706042421
[ 43.9160914  81.3163492]
861821706042831
[  36.58344205  101.85557902]
861821706043881
[  39.81934489  116.15197863]
861821706043931
[  26.56189854  107.9654248 ]
861821706045011
[  25.16334637  113.47160416]
861821706045101
[  28.95016799  106.93119689]
861821706046941
[  26.55916165  106.69400732]
861821706047261
[  32.21486219  110.24649306]
861821706048511
[  23.62302411  102.82974078]
861821706050011
[  31.13915329  121.34637758]
861821706051891
[  37.94449127  102.65531009]
861821706051971
[  31.55679971  120.34449201]
861821706052331
[  29.55401333  103.71502772]
861821706052401
[  29.36000591  104.76226676]
861821706052861
[  34.77620953  111.19815748]
861821706053401
[  25.0355497   102.69385911]
861821706053831
[  32.00256037  120.84600735]
861821706054

...

[  41.2812903   123.76901831]
891641610010271
[  30.03375084  121.6118902 ]
891641610010791
[  29.7657362   118.26532977]
891641610011241
[  27.56128952  116.63861417]
891641610011791
[  22.96460307  113.01146448]
891641610011931
[  27.96276777  120.74985853]
891641610012051
[  40.07994851  116.31298411]
891641610012311
[  31.95903312  118.85967341]
891641610013131
[  30.54318282  114.65210625]
891641610013141
[  25.83017834  104.50093675]
891641610013571
[  31.71646939  120.06488986]
891641610013981
[  31.63555049  119.6401172 ]
891641610014161
[  28.42812226  121.33798686]
891641610015051
[  40.05233795  116.31201491]
891641610015751
[  39.92860746  116.33399822]
891641610017381
[  27.17714872  120.36922269]
891641610017761
[  32.04790688  118.78940046]
891641610017911
[  28.32617026  120.99790616]
891641610018041
[  30.77738144  120.74491268]
891641610018241
[  30.64477237  114.14736771]
891641610018681
[  24.40607052  111.56239801]
891641610018831
[  31.79494413  119.97944892]
8916

[  36.64735636  117.02018457]
891691708003871
[  28.20230786  121.02516282]
891691708004451
[  23.13269026  113.35800243]
891691708005381
[  26.63488763  106.64520904]
891691708005581
[  30.28383901  120.04253045]
891691708005721
[  22.96586981  113.7271628 ]
891691708005741
[  30.28063816  120.12985529]
891691708005941
[  39.221643    115.77341417]
891691708006191
[  40.04430496  116.59388235]
891691711001531
[  27.86318868  120.78874281]
891701709000041
[  30.35834492  120.14619485]
891701709000201
[  30.34824741  120.34505641]
891701709000301
[  22.82538383  114.06290119]
891701709000491
[  30.26462544  120.47026717]
891701709000921
[  31.75564376  120.03871046]
891701709000961
[  31.87139897  120.52814717]
891701709001881
[  28.19758204  113.00783577]
891701709004021
[  26.5664367   106.47499083]
891701709004231
[  40.0593804   116.41793607]
891701709004641
[  27.28313633  105.29173173]
891701709004901
[  31.39203205  121.49725641]
891701709005141
[  31.39545098  121.36475388]
8917

[  30.96675127  118.74959023]
891941605008621
[  31.78012269  119.96781504]
895851711001200
[  30.93376982  121.67863247]
895851711001598
[  28.5884479   121.33767214]
895851711003404
[  23.11618728  113.40941129]
895851711004600
[  22.78384313  108.32670408]
895851711004782
[  29.68582606  106.56889247]
998851710000231
[  25.06657999  121.53358104]
998851710001471
[  25.03239005  121.290667  ]
998851710001531
[  23.96277131  120.97436972]
358962079107966
[  43.9498076   125.31301469]
358962079120563
[  43.80112358  125.28611014]
698851707000191
[  24.94060175  121.26203785]
815821801000740
[  23.35573727  116.63853408]
851181601098191
[  22.94492776  113.08690155]
851181601098271
[  24.66649493  102.16755836]
861021509011351
[  21.45891598  109.14904528]
861021510007852
[ 44.28869309  86.05978531]
861021510020642
[  29.28642113  120.21556066]
861021510025792
[  26.55669223  106.702102  ]
861021510025842
[  38.49706697  115.58739028]
861021510042922
[  29.36051599  113.17888361]
861081

[  34.78812328  113.63585041]
861691610017611
[  29.93645912  103.70395256]
861691610019161
[  27.26147792  111.74193232]
861691610019581
[  36.78905017  119.48286549]
861691610021271
[  38.9687188   121.55655555]
861691610021411
[  37.47309467  117.98802178]
861691610021611
[  34.22290962  108.87922923]
861691610021911
[  32.08794699  112.20219623]
861691610022261
[  22.91940858  113.98040674]
861691610023311
[  40.04639145  116.24087697]
861691610024721
[  31.40569911  121.42956494]
861691610024791
[  34.2285001   108.94688419]
861691610024801
[  31.0418128   107.51725373]
861691610024851
[  25.50266983  103.77139333]
861691610026241
[  31.63262636  120.83775216]
861691610026981
[  30.63910907  114.10538024]
861691610027061
[  24.34517291  102.54654673]
861691610027121
[  31.64731777  120.80758752]
861691610027181
[  39.18234584  117.09650069]
861691610027711
[  31.22651314  105.39134357]
861691610031411
[  34.36588771  107.17193939]
861691610031751
[  31.33415871  121.27412758]
8616

[  37.23996378  117.93192388]
861691701004921
[  24.06443833  104.146126  ]
861691701005991
[  38.94373559  121.55767627]
861691701007351
[  30.59454371  103.9900999 ]
861691701007391
[  34.35562003  107.29540693]
861691701007801
[  31.34454132  120.52199037]
861691701007881
[  36.9227777  119.4015692]
861691701008411
[  24.96704933  103.07054222]
861691701008681
[  26.05315964  105.76748564]
861691701008861
[  30.65948007  103.96524665]
861691701008901
[  37.8043152   114.84167303]
861691701009231
[  30.19250751  105.84351237]
861691701009511
[  38.94889572  121.58324584]
861691701009961
[  25.1003743  102.7476773]
861691701011511
[  25.91289145  103.26371034]
861691701011571
[  24.3764928   102.34673131]
861691701011871
[  30.80377882  103.90843255]
861691701012011
[  27.88024996  120.7894051 ]
861691701012181
[  30.47842842  104.07377818]
861691701012751
[  32.56594483  120.5926287 ]
861691701012801
[  31.37127085  119.82728351]
861691701014371
[  30.55801137  104.00076748]
86169170